In [10]:
#;sudo apt-get update

In [14]:
#ENV["GRDIR"]=""
#Pkg.build("GR")

In [21]:
#;sudo apt-get install dvipng -y

In [2]:
#]add https://github.com/JuliaEnergy/PowerDynamics.jl

In [8]:
#using Pkg
#Pkg.add("DiffEqBase")
#Pkg.add("Plots")
#Pkg.add("LaTeXStrings")
#Pkg.add("OrdinaryDiffEq")
#Pkg.add("Setfield")

# Loading Packages necessary for simulation

In [4]:
using Pkg;
Pkg.instantiate();
cd(@__DIR__);
using PowerDynamics;
using Plots;
using OrdinaryDiffEq: ODEProblem, Rodas4, solve;
include("plotting.jl");
include("helpers.jl");

  Updating registry at `/opt/julia/registries/General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`


# Model Building

In [3]:
#powergrid = read_powergrid("ieee-14-minimal.json", Json)
#operationpoint = find_operationpoint(powergrid);

node_list=[
    SwingEqLVS(H=5.148, P=2.32, D=0.0063662, Ω=314.159, Γ=2, V=1), 
    SlackAlgebraic(U=1),
    SwingEqLVS(H=6.54, P=-0.942, D=0.0063662, Ω= 314.159, Γ=2, V=1),
    PQAlgebraic(P=-0.478, Q=-0.0), 
    PQAlgebraic(P=-0.076, Q=-0.016), 
    SwingEqLVS(H=5.06, P=-0.112, D=0.0063662, Ω=314.159, Γ=2, V=1), 
    PQAlgebraic(P=-0.0, Q=-0.0), 
    SwingEqLVS(H=5.06, P=0.0, D=0.0063662, Ω=314.159, Γ=2, V=1), 
    PQAlgebraic(P=-0.295,Q= -0.166), 
    PQAlgebraic(P=-0.09, Q=-0.058), 
    PQAlgebraic(P=-0.035,Q= -0.018), 
    PQAlgebraic(P=-0.061, Q=-0.016), 
    PQAlgebraic(P=-0.135, Q=-0.058), 
    PQAlgebraic(P=-0.149, Q=-0.05)
];

line_list=[
    StaticLine(from=1, to=2, Y=4.99913-15.2631im), 
    StaticLine(from=1, to=5, Y=1.0259-4.23498im), 
    StaticLine(from=2, to=3, Y=1.13502-4.78186im), 
    StaticLine(from=2, to=4, Y=1.68603-5.11584im), 
    StaticLine(from=2, to=5, Y=1.70114-5.19393im), 
    StaticLine(from=3, to=4, Y=1.98598-5.06882im), 
    StaticLine(from=4, to=5, Y=6.84098-21.5786im), 
    StaticLine(from=4, to=7, Y=0.0-4.78194im), 
    StaticLine(from=4, to=9, Y=0.0-1.79798im), 
    StaticLine(from=5, to=6, Y=0.0-3.96794im), 
    StaticLine(from=6, to=11,Y=1.95503-4.09407im), 
    StaticLine(from=6, to=12, Y=1.52597-3.17596im), 
    StaticLine(from=6, to=13, Y=3.09893-6.10276im), 
    StaticLine(from=7, to=8, Y=0.0-5.67698im), 
    StaticLine(from=7, to=9, Y=0.0-9.09008im), 
    StaticLine(from=9, to=10, Y=3.90205-10.3654im), 
    StaticLine(from=9, to=14, Y=1.42401-3.02905im), 
    StaticLine(from=10, to=11,Y= 1.88088-4.40294im), 
    StaticLine(from=12, to=13, Y=2.48902-2.25197im), 
    StaticLine(from=13, to=14, Y=1.13699-2.31496im)
];

powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

UndefVarError: UndefVarError: SwingEqLVS not defined

In [3]:
# reduce inertia of power grid
nodes_reduced_inertia = [1,3,6,8]
scaling_factor=0.3
powergrid_inertia_reduced = change_inertia(scaling_factor,nodes_reduced_inertia,powergrid);

## Line tripping

In [4]:
disturbed_nodes=[6,12]
simulation_time=(0.,5.)
line_fault=LineFault(disturbed_nodes[1],disturbed_nodes[2]);
faulty_grid = line_fault(powergrid);
problem = ODEProblem{true}(rhs(faulty_grid),operationpoint.vec,simulation_time)
sol_lf = solve(problem,Rodas4(autodiff=false),saveat=1e-4)#,callback=cb)
result_lf=PowerGridSolution(sol_lf, faulty_grid);
faulty_grid2 = line_fault(powergrid_inertia_reduced);
problem2 = ODEProblem{true}(rhs(faulty_grid2),operationpoint.vec,simulation_time)
sol_lf2 = solve(problem2,Rodas4(autodiff=false),saveat=1e-4)#,callback=cb)
result_lf2=PowerGridSolution(sol_lf2, faulty_grid2);

In [5]:
plot_res_compare(result_lf,result_lf2,faulty_grid,faulty_grid2,disturbed_nodes[1])

In [6]:
determine_rocof_nadir(faulty_grid,sol_lf)

([0.00169307, 0.00871679, 0.014888, 0.0109931], [0.0318572, 0.117851, 0.183799, 0.127663])

## Sudden Loss of Load

In [10]:
include("simulate_pd.jl")
timespan= (0.,5);
disturbed_node=4;
powergrid = PowerGrid(node_list, line_list);
operationpoint = find_operationpoint(powergrid);
pd = PowerPerturbation(node_number=disturbed_node,fraction=0.5, tspan_fault=(0.5,5));

sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan)
plot_res(result_pd,powergrid,disturbed_node)

In [11]:
determine_rocof_nadir(powergrid,sol_pd)

([0.0154946, 0.0430902, 0.0636049, 0.0788319], [0.444068, 0.787171, 0.974583, 1.05932])